In [1]:
import pandas as pd
import os

# Directory containing the CSX review files
directory = "./reviews"

# List to store DataFrames from each file
dfs = []

# Loop through each file in the directory
for filename in os.listdir(directory):
    if filename.endswith(".csv"):
        # Read the CSV file into a DataFrame
        df = pd.read_csv(os.path.join(directory, filename))
        # Drop rows with missing values (if any)
        df = df.dropna()
        # Append the DataFrame to the list
        dfs.append(df)

# Concatenate all DataFrames into a single DataFrame
if dfs:
    combined_df = pd.concat(dfs, ignore_index=True)
else:
    print("No CSV files found in the 'reviews' directory.")

for idx, df in enumerate(dfs, start=1):
    print(f"DataFrame {idx}: Number of rows: {len(df)}")



DataFrame 1: Number of rows: 520
DataFrame 2: Number of rows: 1020
DataFrame 3: Number of rows: 860
DataFrame 4: Number of rows: 700
DataFrame 5: Number of rows: 680
DataFrame 6: Number of rows: 1020
DataFrame 7: Number of rows: 1020
DataFrame 8: Number of rows: 1020
DataFrame 9: Number of rows: 920
DataFrame 10: Number of rows: 1020
DataFrame 11: Number of rows: 1020
DataFrame 12: Number of rows: 1020
DataFrame 13: Number of rows: 1020
DataFrame 14: Number of rows: 900
DataFrame 15: Number of rows: 1020
DataFrame 16: Number of rows: 640
DataFrame 17: Number of rows: 420
DataFrame 18: Number of rows: 820
DataFrame 19: Number of rows: 840
DataFrame 20: Number of rows: 840
DataFrame 21: Number of rows: 1020
DataFrame 22: Number of rows: 1020
DataFrame 23: Number of rows: 1020
DataFrame 24: Number of rows: 1020
DataFrame 25: Number of rows: 620


In [2]:
df.head(5) 

brand               model  \
0    WD  WDBAGF0010BBL-WESN   
1    WD  WDBAGF0010BBL-WESN   
2    WD  WDBAGF0010BBL-WESN   
3    WD  WDBAGF0010BBL-WESN   
4    WD  WDBAGF0010BBL-WESN   

                                             product                   date  \
0  WD - My Passport 1TB External USB Type-C Porta...   Nov 20, 2020 2:10 AM   
1  WD - My Passport 1TB External USB Type-C Porta...    Oct 6, 2023 4:15 PM   
2  WD - My Passport 1TB External USB Type-C Porta...  Apr 17, 2024 11:37 PM   
3  WD - My Passport 1TB External USB Type-C Porta...    Jan 5, 2024 6:20 PM   
4  WD - My Passport 1TB External USB Type-C Porta...    Jan 8, 2024 6:05 PM   

                                              review  
0  Since my MacBook was about to out of space, I ...  
1  Love this product! It is lightening speed and ...  
2  Excellent purchase. Lots and lots of memories ...  
3  Been using it for several months. No corrupted...  
4  easy setup, very easy to use, can't believe ho...

In [3]:
print(len(df))
print(len(combined_df))


620
22020


In [4]:
df.dtypes

brand      object
model      object
product    object
date       object
review     object
dtype: object

In [5]:
new_df = pd.DataFrame()

In [6]:
# Sentence Splitting
from nltk.tokenize import sent_tokenize
from cleantext import clean

# Initialize lists to store data
product = []
title = []  # If needed
review = []
date = []
review_id = []

# Loop through each row in the DataFrame
for index, row in combined_df.iterrows():
    sentences = sent_tokenize(row['review'])
    for sentence in sentences:
        product.append(row['product'])
        # title.append(row['title'])  # If needed
        review.append(clean(sentence, no_emoji=True))
        date.append(row['date'])
        review_id.append(index)  # Use the index as review_id

# Create a new DataFrame with the collected data
new_df = pd.DataFrame({
    'review_id': review_id,
    'product': product,
    # 'title': title,  # If needed
    'review': review,
    'date': date
})


In [7]:
new_df.head(5) 

review_id                                            product  \
0          0  CORSAIR - MP600 PRO LPX 2TB Internal SSD PCIe ...   
1          0  CORSAIR - MP600 PRO LPX 2TB Internal SSD PCIe ...   
2          0  CORSAIR - MP600 PRO LPX 2TB Internal SSD PCIe ...   
3          0  CORSAIR - MP600 PRO LPX 2TB Internal SSD PCIe ...   
4          0  CORSAIR - MP600 PRO LPX 2TB Internal SSD PCIe ...   

                                             review                  date  
0  need extra storage for your ps5 look no further.  Jun 30, 2023 8:26 PM  
1                     caught this on sale for $129.  Jun 30, 2023 8:26 PM  
2                             well worth the money.  Jun 30, 2023 8:26 PM  
3                                      zero issues.  Jun 30, 2023 8:26 PM  
4                     took about 2 mins to install.  Jun 30, 2023 8:26 PM

In [8]:
print(len(new_df))

88644


In [9]:
#Text Preprocessing for aspect extraction
import string
import emoji
import re
import nltk
from textblob import TextBlob
from nltk.corpus import wordnet
from nltk.metrics import edit_distance
from nltk.stem.porter import PorterStemmer
from nltk.tokenize import word_tokenize

# spacy for lemmatization
import spacy
nlp = spacy.load('en_core_web_sm', disable=['parser', 'ner'])

stopwords = nltk.corpus.stopwords.words('english')

def preprocess(text):
    
    #1. Generating the list of words in the tweet (hastags and other punctuations removed)
    text_blob = TextBlob(text)
    text = ' '.join(text_blob.words)
    
    #2. clean the number 
    text = re.sub(r'[0-9]', '', text)
    
    #3. lower the text
    text = text.lower()
    
    #4. conver the emoji to text form
    text = emoji.demojize(text)
    
    #5. remove punctuation 
    for punctuation in string.punctuation:
        text = text.replace(punctuation, '')
    
    #6. tokenize the text
    text = word_tokenize(text)
    
    #7. remove empty token
    text = [t for t in text if len(t) > 0]
    
    #8. remove non-alphabetical token
    text = [t for t in text if t.isalpha()]
    
    #9. replace the negation token
    replacer  = AntonymReplacer()
    text = replacer.replace_negations(text)
    
    #10. remove the stopwords
    text = [i for i in text if i not in stopwords]
    
    #11. stem the text
    #porter_stemmer = PorterStemmer()
    #text = [porter_stemmer.stem(w) for w in text]
    
    #11. lemmatize the text
    text = lemmatization(text, allowed_postags=['NOUN', 'ADJ', 'VERB', 'ADV'])
    
    return text


def lemmatization(sent, allowed_postags=['NOUN', 'ADJ', 'VERB', 'ADV']):
    doc = nlp(" ".join(sent)) 
    texts_out = [token.lemma_ for token in doc if token.pos_ in allowed_postags]
    return texts_out

class AntonymReplacer(object):
    def replace(self, word, pos=None):
        antonyms = set()

        for syn in wordnet.synsets(word, pos=pos):
            for lemma in syn.lemmas():
                for antonym in lemma.antonyms():
                    antonyms.add(antonym.name())

        if len(antonyms) == 1:
            return antonyms.pop()
        else:
            return None

    def replace_negations(self, sent):
        i, l = 0, len(sent)
        words = []

        while i < l:
            word = sent[i]

            if word == 'not' and i+1 < l:
                ant = self.replace(sent[i+1])

                if ant:
                    words.append(ant)
                    i += 2
                    continue

            words.append(word)
            i += 1

        return words

In [10]:
print(new_df.iloc[1,3])
print(type(new_df.iloc[1,3]))
print(preprocess( new_df.iloc[1,3]))

Jun 30, 2023 8:26 PM
<class 'str'>
['pm']


In [11]:
#Preprocess the input data
cleaned_text = []
counter = 1

for text in new_df["review"]:
    print(f'Preprocessing row {counter}')
    counter+=1
    cleaned_text.append(preprocess(str(text)))

new_df["Clean"] = cleaned_text
new_df = new_df.dropna()

new_df.to_excel("preprocessed_data.xlsx")
print('Preprocessing done.')

Preprocessing row 1
Preprocessing row 2
Preprocessing row 3
Preprocessing row 4
Preprocessing row 5
Preprocessing row 6
Preprocessing row 7
Preprocessing row 8
Preprocessing row 9
Preprocessing row 10
Preprocessing row 11
Preprocessing row 12
Preprocessing row 13
Preprocessing row 14
Preprocessing row 15
Preprocessing row 16
Preprocessing row 17
Preprocessing row 18
Preprocessing row 19
Preprocessing row 20
Preprocessing row 21
Preprocessing row 22
Preprocessing row 23
Preprocessing row 24
Preprocessing row 25
Preprocessing row 26
Preprocessing row 27
Preprocessing row 28
Preprocessing row 29
Preprocessing row 30
Preprocessing row 31
Preprocessing row 32
Preprocessing row 33
Preprocessing row 34
Preprocessing row 35
Preprocessing row 36
Preprocessing row 37
Preprocessing row 38
Preprocessing row 39
Preprocessing row 40
Preprocessing row 41
Preprocessing row 42
Preprocessing row 43
Preprocessing row 44
Preprocessing row 45
Preprocessing row 46
Preprocessing row 47
Preprocessing row 48
P

In [12]:
print(type(cleaned_text))

<class 'list'>


In [14]:
# #Extract 100k from original dataset for BERTopic, skip this if the dataset is < 100k
# import pandas as pd
# pd.read_excel("preprocessed_data.xlsx").sample(n=100000).to_excel("extracted_data.xlsx", index=False)

In [15]:
import pandas as pd
#extracted_data = pd.read_excel("D:/research/data/reviews/extracted_data.xlsx")
extracted_data = pd.read_excel("preprocessed_data.xlsx")

In [16]:
#LDA model training

import gensim.corpora as corpora
import gensim.models as models

from ast import literal_eval
from pprint import pprint

data_words = []
for x in extracted_data['Clean']:
    data_words.append(literal_eval(x))

# Create Dictionary
id2word = corpora.Dictionary(data_words)
# Create Corpus
texts = data_words
# Term Document Frequency
corpus = [id2word.doc2bow(text) for text in texts]

# number of topics
num_topics = 50
num_words = 10

# Build LDA model
lda_model1 =models.LdaMulticore(corpus=corpus,
                              id2word=id2word,
                              num_topics=num_topics)



In [18]:
#save LDA Model
import pickle
topics = lda_model1.print_topics(num_topics=num_topics, num_words=num_words)
topic_list = []
for topic in topics:
  topic_list.append(topic[1])

#df['topics1'] = topic_list1
df_topics = pd.DataFrame(topic_list,  columns =['topics'])

df_topics.to_excel("LDA_topics.xlsx")
pickle.dump(lda_model1, open('LDA_model.model', 'wb'))#save lda model
pickle.dump(id2word, open('LDA_model.dict', 'wb'))#save dictionary
pickle.dump(corpus, open('LDA_model.corpus', 'wb'))#save corpus



In [19]:
pprint(lda_model1.print_topics())
doc_lda = lda_model1[corpus]

[(42,
  '0.030*"storage" + 0.027*"use" + 0.023*"speed" + 0.021*"need" + '
  '0.016*"great" + 0.015*"write" + 0.013*"read" + 0.012*"buy" + 0.012*"file" + '
  '0.012*"good"'),
 (44,
  '0.032*"drive" + 0.026*"speed" + 0.023*"good" + 0.021*"easy" + 0.020*"buy" + '
  '0.017*"fast" + 0.015*"install" + 0.012*"get" + 0.012*"storage" + '
  '0.011*"use"'),
 (10,
  '0.028*"speed" + 0.026*"drive" + 0.023*"use" + 0.019*"fast" + 0.017*"ssd" + '
  '0.015*"go" + 0.015*"storage" + 0.012*"feature" + 0.012*"power" + '
  '0.012*"technology"'),
 (25,
  '0.031*"drive" + 0.028*"use" + 0.018*"game" + 0.016*"laptop" + 0.015*"speed" '
  '+ 0.014*"performance" + 0.013*"pc" + 0.012*"ssd" + 0.011*"new" + '
  '0.011*"issue"'),
 (33,
  '0.033*"drive" + 0.022*"slow" + 0.019*"bit" + 0.019*"new" + 0.017*"go" + '
  '0.016*"use" + 0.015*"old" + 0.015*"device" + 0.014*"speed" + 0.014*"hard"'),
 (2,
  '0.038*"well" + 0.023*"come" + 0.022*"drive" + 0.017*"year" + 0.015*"get" + '
  '0.015*"much" + 0.014*"storage" + 0.014*"la

In [5]:
import pickle

lda_model_file = 'LDA_model.model' 
loaded_lda_model = pickle.load(open(lda_model_file, 'rb')) #load trained model
loaded_dictionary = pickle.load(open('LDA_model.dict', 'rb')) #load dictionary 
loaded_corpus = pickle.load(open('LDA_model.corpus', 'rb')) # load corpus


In [6]:
import pyLDAvis
import pyLDAvis.gensim_models as gensimvis

pyLDAvis.enable_notebook()
vis = gensimvis.prepare(loaded_lda_model, loaded_corpus, loaded_dictionary)


In [7]:
vis

PreparedData(topic_coordinates=              x         y  topics  cluster      Freq
topic                                               
6     -0.034966  0.008111       1        1  2.928009
27     0.005640  0.069239       2        1  2.663562
19     0.061736 -0.080206       3        1  2.655818
29     0.092806  0.005985       4        1  2.647081
7      0.015773  0.006993       5        1  2.558312
46    -0.064332  0.101112       6        1  2.556408
32     0.034524 -0.004357       7        1  2.499268
33    -0.024407 -0.082147       8        1  2.445970
17     0.077139 -0.018454       9        1  2.426046
40     0.007889  0.061468      10        1  2.367975
36    -0.045967 -0.065902      11        1  2.336412
28    -0.013120 -0.019996      12        1  2.300896
2     -0.085139 -0.095973      13        1  2.296611
15    -0.047652 -0.020909      14        1  2.293021
23    -0.049454  0.059322      15        1  2.229393
37    -0.037450  0.050151      16        1  2.213379
38    -0.005088  0.010517      17        1  2.165826
30    -0.014029 -0.040490      18        1  2.162397
26    -0.003342 -0.007431      19        1  2.149925
25     0.027234  0.022317      20        1  2.096470
18     0.034111 -0.020361      21        1  2.085759
49    -0.061730 -0.049131      22        1  2.067315
11    -0.011144  0.003859      23        1  2.065178
45    -0.026219  0.001799      24        1  2.059533
14     0.041483 -0.034143      25        1  2.000899
3      0.050210  0.007889      26        1  1.999002
43     0.044487 -0.051499      27        1  1.996784
13    -0.013840 -0.053660      28        1  1.994142
42    -0.068106  0.000804      29        1  1.949913
39     0.023181  0.015198      30        1  1.941294
0      0.046687  0.014349      31        1  1.927639
4      0.031536  0.016990      32        1  1.887351
35    -0.012149  0.047164      33        1  1.877435
16    -0.035431  0.014921      34        1  1.836920
31    -0.047882  0.005059      35        1  1.828384
24     0.030441 -0.024314      36        1  1.800049
48    -0.057083 -0.003971      37        1  1.733201
8     -0.003228  0.011236      38        1  1.721042
44     0.003564  0.017699      39        1  1.706002
9     -0.003134  0.037287      40        1  1.693616
47     0.072622  0.005614      41        1  1.613178
41    -0.016491  0.004475      42        1  1.595778
5     -0.007243  0.007673      43        1  1.487558
21     0.024849 -0.020336      44        1  1.442812
12     0.016506 -0.029562      45        1  1.366927
22    -0.040438  0.018115      46        1  1.353893
34     0.028698  0.026730      47        1  1.312726
10    -0.002212  0.004871      48        1  1.261648
1      0.051832  0.043222      49        1  1.229774
20     0.008330  0.022676      50        1  1.171466, topic_info=         Term          Freq         Total Category  logprob  loglift
83      drive  18556.000000  18556.000000  Default  30.0000  30.0000
65       good   6458.000000   6458.000000  Default  29.0000  29.0000
112      work   6605.000000   6605.000000  Default  28.0000  28.0000
3     storage   8034.000000   8034.000000  Default  27.0000  27.0000
747   western   1078.000000   1078.000000  Default  26.0000  26.0000
..        ...           ...           ...      ...      ...      ...
57   capacity     38.120617   1640.155780  Topic50  -5.1767   0.6851
174     speed     44.264822   6816.610727  Topic50  -5.0273  -0.5900
16      price     41.763244   4750.355124  Topic50  -5.0855  -0.2870
64        get     41.045561   5326.186847  Topic50  -5.1028  -0.4188
7        well     39.285207   3879.999246  Topic50  -5.1466  -0.1458

[3303 rows x 6 columns], token_table=      Topic      Freq  Term
term                       
1325      4  0.044326   aaa
1325      6  0.088651   aaa
1325     11  0.088651   aaa
1325     14  0.044326   aaa
1325     19  0.044326   aaa
...     ...       ...   ...
1448     38  0.034817  zone
1448     39  0.034817  zone
1448     42  0.034817  zone
1448     44  0.069635  zone

In [9]:

# Extract topics
topics = loaded_lda_model.show_topics(num_topics=50, num_words=10, formatted=False)

# Create a list to store the topic strings
topic_strings = []

# Format and print the topics
for topic_num, topic_terms in topics:
    topic_str = f"Topic {topic_num}: " + ", ".join([f"{word}" for word, prob in topic_terms])
    topic_strings.append(topic_str)
    print(topic_str)

Topic 0: drive, storage, easy, use, ssd, fast, need, great, transfer, space
Topic 1: drive, great, buy, ssd, hard, good, work, game, upgrade, performance
Topic 2: well, come, drive, year, get, much, storage, last, price, work
Topic 3: drive, disk, issue, less, ssd, time, find, show, give, storage
Topic 4: drive, good, fast, ssd, work, game, storage, use, buy, well
Topic 5: store, drive, use, storage, movie, new, ssd, device, easy, old
Topic 6: file, storage, speed, use, fast, video, product, game, drive, run
Topic 7: drive, wd, get, speed, storage, ssd, read, fast, write, need
Topic 8: performance, drive, use, speed, much, buy, ssd, recommend, great, need
Topic 9: drive, ssd, storage, buy, speed, upgrade, use, hard, also, game
Topic 10: speed, drive, use, fast, ssd, go, storage, feature, power, technology
Topic 11: use, drive, ssd, storage, great, get, speed, new, heat, game
Topic 12: drive, use, good, fast, ssd, quick, purchase, pro, great, get
Topic 13: work, drive, great, make, well

In [ ]:
# StoragePerformance:

# Terms: storage, ssd, fast, speed, transfer, space, feature, technology.
# ProductReliability:

# Terms: drive, well, year, last, issue, disk, less, find, show, give.
# UserExperience:

# Terms: easy, use, need, great, work, game, file, run, install.
# PriceAffordability:

# Terms: price, buy, much, recommend, purchase, lose.
# CompatibilityConnectivity:

# Terms: store, device, old, laptop, new, pc, external, hdd, connect, system.
# TaskPerformance:

# Terms: game, backup, boot, window, load, instal, run, system, download, space.
# BuildQuality:

# Terms: good, well, purchase, heat, make, case, recommend, quality.
# CustomerSupport:

# Terms: problem, issue, help.
# VersatilityAdaptability:

# Terms: work, use, several, feature, need, work, perform.
# UserSatisfaction:

# Terms: happy, satisfied, recommend, worth, love, glad, please.